# VDF Function Search For edges

In order to apply any system optimal route assignment algorithms, volume delay functions for each edge in the graph has to be defined. This will be estimated from volume travel time pairs recorded from 4 simulations runs, each with 20 iterations. The travel volume was scaled from 10% to 100% at a step of 10% per iteration, so the the final 10 iterations of each run are all at 100% volume.

In [1]:
import qgrid
import pandas as pd
import numpy as np
from ipywidgets import interact, interact_manual
import ipywidgets as widgets
from IPython.display import display, clear_output, Image
from typing import Tuple, Sequence

from os import path
import pickle

# Standard plotly imports
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import iplot, init_notebook_mode
# Using plotly + cufflinks in offline mode
import cufflinks
cufflinks.go_offline(connected=True)
init_notebook_mode(connected=True)

## Load and display the data

In [2]:
def read_edge_vol_delay(in_files: Sequence[str]) -> pd.DataFrame:
    # import here to not polute the notebook namespace
    from EdgeRouteParser import dynamic_assignment_file_read, timevol_table, functions_expansion
    import pathos.multiprocessing as mp
    
    in_files = [file for file in in_files if '_' in path.split(file)[-1]]
    with mp.Pool() as pool:
        tables = pool.map(functions_expansion(dynamic_assignment_file_read,
                                              lambda tbd: tbd['VolTime'],
                                              timevol_table
                                              ), in_files)

    sim_itr = [int(path.basename(fr).split('.')[0].split('_')[-1])
               for fr in in_files]
    sim_dem = [float(path.split(path.split(fr)[0])[-1]
                     .replace('Vol', '').replace('per', '')) / 100 for fr in in_files]
    for itr, dem, table in zip(sim_itr, sim_dem, tables):
        table['ITR'] = itr
        table['Demand'] = dem

    return pd.concat(tables)

In [3]:
# load from cache if exists
try:
    edge_volume_time = pd.read_pickle("edge_volume_time.pkl.gz")
except FileNotFoundError:
    from EdgeRouteParser import files_by_ext
    files = files_by_ext(path.abspath(r"..\Urban Freeway Dyn Assign Redmond.US"), 'bew')
    files = [file for file in files if '_' in path.split(file)[-1]]
    edge_volume_time = read_edge_vol_delay(files)
    edge_volume_time = edge_volume_time.rename(index=str, columns={"NO": "Edge", "TRAVTMNEW": "TravelTime", "VOLNEW": 'Volume'})
    edge_volume_time.to_pickle("edge_volume_time.pkl.gz", compression="gzip")
    del files

### Simulation results

|     Edge     |   VehType    |              Period                         |        TravelTime         |       Volume        | ITR                  | Demand |
|:----------:|:------------:|:-------------------------------------------:|:------------------------:|:------------------:|:---------------------:|:------:|
|edge number | vehicle type | simulation data sample period (10 min each) | average edge travel time | 10 min volume count | simulation iteration | DTA demand proportion |


In [4]:
qgrid.show_grid(edge_volume_time, grid_options={'editable': False,'maxVisibleRows':8})

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': True, 'defau…

## Create interactive travel time vs 10 min volume plot

Create interactive widgets for filtering data for analysis

In [5]:
style = {'description_width': 'initial'}
layout = widgets.Layout(width='95%')

demand_max = edge_volume_time['Demand'].max()
demand_min = edge_volume_time['Demand'].min()

edge_wig = widgets.IntSlider(min=edge_volume_time['Edge'].min(),
                             max=edge_volume_time['Edge'].max(),
                             step=1,
                             description='Network Edge:',
                             value=75,
                             style=style,
                             layout=layout,
                             continuous_update=False)

veh_type_wig = widgets.Dropdown(options=list(edge_volume_time['VehType'].unique()),
                                description='Vehicle Type:',
                                value=list(edge_volume_time['VehType'].unique())[0],
                                style=style)

ITR_wig = widgets.IntRangeSlider(min=edge_volume_time['ITR'].min(),
                                 max=edge_volume_time['ITR'].max(),
                                 step=1,
                                 value=(5, 20),
                                 description='Sim Iteration:',
                                 style=style,
                                 layout=layout,
                                 continuous_update=False)

Period_wig = widgets.IntRangeSlider(min=edge_volume_time['Period'].min(),
                                    max=edge_volume_time['Period'].max(),
                                    step=1,
                                    value=(2, 6),
                                    description='DTA Period:',
                                    style=style,
                                    layout=layout,
                                    continuous_update=False)

Demand_wig = widgets.FloatRangeSlider(max=demand_max+0.1,
                                      min=demand_min-0.1,
                                      value=(0.1, 1.5),
                                      step=0.1,
                                      description='DTA Traffic Demand:',
                                      style=style,
                                      layout=layout,
                                      readout_format='.0%',
                                      continuous_update=False)

Function for filtering the data based on the above interactive widgets

In [6]:
from collections.abc import Iterable

def VD_data_filter(edge=None,
                   veh_type=list(edge_volume_time['VehType'].unique())[0],
                   itr=(edge_volume_time['ITR'].min(),
                        edge_volume_time['ITR'].max()),
                   period=(edge_volume_time['Period'].min(),
                           edge_volume_time['Period'].max()),
                   demand=(edge_volume_time['Demand'].min(),
                           edge_volume_time['Demand'].max()),
                   frame=edge_volume_time):
    
    # filter for all edges
    if edge is None:
        edge_filter = pd.Series(data=[True] * frame.shape[0], index=frame.index)
    elif isinstance(edge, Iterable):
        edge_filter = frame['Edge'].isin(edge)
    else:
        edge_filter = frame['Edge'] == edge
    

    # Filter for plotting
    filtered_frame = frame.loc[edge_filter &
                           (frame['VehType'] == veh_type) &
                           (frame['ITR'] >= itr[0]) &
                           (frame['ITR'] <= itr[1]) & 
                           (frame['Period'] >= period[0]) &
                           (frame['Period'] <= period[1]) & 
                           (frame['Demand'] >= demand[0]) &
                           (frame['Demand'] <= demand[1]),:]


    return filtered_frame

### Interactive scatter plot travel time vs traffic volume

In [7]:
# function to turn dataframe to plotly plot
def edge_VD_plot(*args, **kwargs) -> dict:
    plotting_frame = VD_data_filter(*args, **kwargs)

    def row_2_text(row):
        row = row[1]
        return "Vol: {}, Time: {:.2f}s<br>".format(row.Volume, row.TravelTime) + \
               "Itr: {}, Period: {}<br>".format(row.ITR, row.Period) + \
               "Demand: {}".format(row.Demand)
    text = [row_2_text(row) for row in plotting_frame.iterrows()]

    # get different iteration series for plotly
    return dict(
        x=plotting_frame.Volume,
        y=plotting_frame.TravelTime,
        mode='markers',
        text=text,
        hoverinfo='text',
        marker=dict(
            color=plotting_frame.Demand,
            cmax=demand_max,
            cmin=demand_min,
            colorbar=dict(title='Sim Demand'),
            colorscale='Portland',
            reversescale=False
        ),
    )


# drop_first_last_wig = widgets.Checkbox(
#     value=True,
#     description='Drop first and last sim period',
#     style=style,
# )

input_wigs = [edge_wig, veh_type_wig, ITR_wig, Period_wig, Demand_wig]

# Create interactive plot
plt_layout = {
    'xaxis': {'title': '10 min Volume (count)', 'rangemode': 'tozero'},
    'yaxis': {'title': "Average Vehicle Travel Time (s)", 'rangemode': 'tozero'},
    'autosize': True,
    'height': 700,
    'hovermode': 'closest',
    'plot_bgcolor': 'white'
    # 'template': 'plotly_dark'
}

vd_plot_fig = go.FigureWidget(data=[go.Scatter(**edge_VD_plot(*[wig.value for wig in input_wigs]))],
                           layout=plt_layout)


def update_plot(_):
    with vd_plot_fig.batch_update():
        updated_data = edge_VD_plot(*[wig.value for wig in input_wigs])
        vd_plot_fig.data[0].x = updated_data['x']
        vd_plot_fig.data[0].y = updated_data['y']
        vd_plot_fig.data[0].text = updated_data['text']
        vd_plot_fig.data[0].marker = updated_data['marker']


[wig.observe(update_plot, names="value") for wig in input_wigs]

out = widgets.VBox(input_wigs + [vd_plot_fig],
                   layout=widgets.Layout(width='100%'))
display(out)

# Testing Volume Delay estimators

In [8]:
# read edge attributes from disk

edge_attr = pd.read_pickle("edges_attr.pkl.gz")

In [9]:
# Compute the average travel speed for each sampling period
Edge_vol_speed = pd.merge(edge_volume_time, edge_attr['Length'],
                          left_on='Edge',
                          right_index=True)
Edge_vol_speed['AvgSpeed'] = \
    Edge_vol_speed['Length'] / Edge_vol_speed['TravelTime'] / 1.467  # convert to miles per hour

## Visualizing travel speed for different edges and demand

To select the appropriate model for marginal cost estimation and to estimate parameters, the rough distribution of of edge flow conditions should be known, so model residual error functions can be speculated on.

In [10]:
# plot the travel speed samples on histogram
@interact(edge=edge_wig,
          itr=ITR_wig,
          period=Period_wig,
          demand=Demand_wig)
def speed_histogram(**kwargs):
    filtered_frame = VD_data_filter(frame=Edge_vol_speed, **kwargs)
    filtered_frame['AvgSpeed'].iplot(kind='histogram', histnorm='percent',
                                     layout={'title': {'text': 'Speed distribution histogram for edge {}'.format(kwargs['edge'])},
                                             'xaxis': {'title': 'Speed (mph)'},
                                             'yaxis': {'title': 'Probability in (%)'}})

interactive(children=(IntSlider(value=75, continuous_update=False, description='Network Edge:', layout=Layout(…

## Edge free flow travel time

In order to anchor any volume delay function to free flow conditions, the mean free flow travel time is required. 

Using the  interactive plot from above, the travel time at 10%-30% traffic demand, during sim period 2 to 6, and after iteration 10 appear to be good data points to estimate free flow time.

Visualise free flow speed distribution given the above selection parameters

In [16]:
free_flow_data = VD_data_filter(veh_type='ALL',
                                itr=(10, 20),
                                period=(2, 6),
                                demand=(0.1, 0.3),
                                frame=Edge_vol_speed).dropna()

free_flow_data.loc[free_flow_data['AvgSpeed'] < 100., 'AvgSpeed'].iplot(
    kind='histogram', bins=40, histnorm='percent',
    layout={'title': {'text': 'Free flow speed distribution histogram'},
            'xaxis': {'title': 'Speed (mph)'},
            'yaxis': {'title': 'Probability (%)'}})

Aggragate values for each edge

In [19]:
aggfunc = [np.mean, np.std]
edge_FF_pivot = free_flow_data.pivot_table(values=['TravelTime', 'Volume', 'AvgSpeed'], index=['Edge'],
                                           aggfunc={'TravelTime': aggfunc,
                                                    'Volume': aggfunc,
                                                    'AvgSpeed': aggfunc+['count']})
edge_FF_pivot.columns = [' '.join(col).strip()
                         for col in edge_FF_pivot.columns.values]

edge_FF_pivot = edge_FF_pivot.rename(
    index=str, columns={'AvgSpeed count': 'Valid data points'})
edge_FF_pivot.columns = edge_FF_pivot.columns.str.replace('AvgSpeed', "FFSpeed")

In [20]:
qgrid.show_grid(edge_FF_pivot, grid_options={'editable': False,'maxVisibleRows':10})

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': True, 'defau…

## Exploring the effects of downstream conditions on link traversal time

In [14]:
edge_attr['DownSteamLinks'] = edge_attr['ToEdges'].map(lambda x: len(x.split(',')))

In [15]:
qgrid.show_grid(edge_attr.loc[:,'DownSteamLinks'])

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': True, 'defau…